In [550]:
%reload_ext autoreload
%autoreload 2
%matplotlib inline
from IPython import display
import pprint
import pymongo
import random
import numpy as np
from bokeh.io import output_notebook
from climatools.cliradlw.cliradlw_latest import *
from climatools.html.html import *
from climatools.spectrum import *
from climatools.atm import *
output_notebook()
pd.set_option('max_colwidth', -1)

Loading BokehJS ...

In [564]:
LINKS.fillna('', inplace=True)
LINKS.sort_index(axis=1, inplace=True)
LINKS.sort_index(axis=0, inplace=True)
display.display(display.HTML(LINKS.to_html(escape=False)))

In [299]:
CLIENT = pymongo.MongoClient(host='localhost', port=27017)

In [508]:
LINKS = pd.DataFrame(columns=pd.MultiIndex(levels=[[], []], labels=[[], []], names=['lblnew band(s)', 'cliradlw band(s)']))
LINKS.index.name = ['absorber(s)']

# 1 x $CO_{2}$

In [551]:
MOL = 'co2'
CONC = 400e-6
COMMITNUMBER = '1013f91'
NV, DV = 1000, .001
ATMPRO = dict(mls=294, saw=257, trp=300)

### Atmosphere composition

In [552]:
atmcomp = AtmComposition.cliradlw_nongreys()
atmcomps_bft = [AtmComposition(gasconcs=atmcomp.gasconcs, gasinbands={b:[MOL]}) 
                for b, gs in atmcomp.gasinbands.items() if MOL in gs]
atmcomps_olp = [AtmComposition(gasconcs=atmcomp.gasconcs, gasinbands={b:gs})
                for b, gs in atmcomp.gasinbands.items() if MOL in gs and len(gs) > 1]

### $CO_2$-only

In [553]:
for c in atmcomps_bft:
    for atmpro in ATMPRO.keys():
        pcli = c.to_cliradparam(atmpro=atmpro, tsfc=ATMPRO[atmpro], commitnumber=COMMITNUMBER)
        #print(pcli.avail_commits(collection=CLIENT.cliradnew.lw))
        dcli = pcli.modeldata_pymongo(collection=CLIENT.cliradnew.lw, commits=[COMMITNUMBER])
        
        plbls = c.to_lblnewparam(bestfit_values=True, dv=DV, nv=NV, atmpro=atmpro, tsfc=ATMPRO[atmpro],
                                 option_wgt_flux=1)
        plbl = plbls[0]
        #print(plbl.avail_commits(collection=CLIENT.lblnew.bestfit_lw))
        dlbl = plbl.modeldata_pymongo(collection=CLIENT.lblnew.bestfit_lw, commits=['a22ab94', 'a06b618'])
        
        ida = show_results(dlbl=dlbl, dcli=dcli, add_idanchor=True, atmpro=atmpro)
        remove_href(idanchor=ida, df=LINKS, dlbl=dlbl, dcli=dcli)
        show_href(idanchor=ida, df=LINKS, dlbl=dlbl, dcli=dcli)

-----------------------------

<a id="28883124707"></a>

[3] {'co2': 0.0004} mls

Run parameters  \
                                CLIRAD   
atmpro                 mls               
band                   [3]               
commitnumber           1013f91           
conc                   -                 
dv                     -                 
klin                   -                 
molecule               {'co2': 0.0004}   
ng_adju                -                 
ng_refs                -                 
nv                     -                 
option_compute_btable  -                 
option_compute_ktable  -                 
option_wgt_flux        -                 
option_wgt_k           -                 
ref_pts                -                 
tsfc                   294               
vmax                   -                 
vmin                   -                 
w_diffuse              -                 
wgt                    -                 

                                                                                 \
                                                                         LBLNEW   
atmpro                 mls                                                        
band                   3a                                                         
commitnumber           a22ab94                                                    
conc                   0.0004                                                     
dv                     0.001                                                      
klin                   6.37556e-24                                                
molecule               co2                                                        
ng_adju                [0, 0, 0]                                                  
ng_refs                [3, 2, 4]                                                  
nv                     1000                                                       
option_compute_btable  0                                                          
option_compute_ktable  0                                                          
option_wgt_flux        1                                                          
option_wgt_k           1                                                          
ref_pts                [[1, 250], [10, 250], [500, 250]]                          
tsfc                   294                                                        
vmax                   620                                                        
vmin                   540                                                        
w_diffuse              [[1.6, 1.6, 1.7], [1.75, 1.75], [1.55, 1.55, 1.6, 1.85]]   
wgt                    [[0.7, 0.3, 0.7], [0.7, 0.6], [0.4, 0.5, 0.8, 0.95]]       

                                                                 Fit parameters  
                                                                      (co2, 3a)  
atmpro                 mls                                                       
band                   3a                                                        
commitnumber           a06b618                                                   
conc                   0.0004                                                    
dv                     0.001                                                     
klin                   6.37556e-24                                               
molecule               co2                                                       
ng_adju                [0, 0, 0]                                                 
ng_refs                [3, 2, 4]                                                 
nv                     1000                                                      
option_compute_btable  0                                                         
option_compute_ktable  1                                                         
option_wgt_flux        1                                                         
option_wgt_k           1                  

CRD                   WGT igg=10                    \
                   flug     fldg    fnetg       flug     fldg    fnetg   
pressure level                                                           
0.000    1     -29.5819  0.0000  -29.5819 -29.7445    0.0000  -29.7445   
180.875  41    -29.9643  1.3874  -28.5769 -30.0983    1.4703  -28.6279   
1013.000 76    -36.2354  16.7573 -19.4781 -36.2354    16.7494 -19.4860   

                 CLIRAD                   CLIRAD - CRD                  
                   flug     fldg    fnetg         flug    fldg   fnetg  
pressure level                                                          
0.000    1     -29.7029  0.0000  -29.7029 -0.1210       0.0000 -0.1210  
180.875  41    -30.0631  1.4828  -28.5803 -0.0987       0.0954 -0.0034  
1013.000 76    -36.2354  16.8385 -19.3969 -0.0000       0.0812  0.0812

...

<a id="38160231653"></a>

[11] {'co2': 0.0004} trp

Run parameters  \
                                CLIRAD   
atmpro                 trp               
band                   [11]              
commitnumber           1013f91           
conc                   -                 
dv                     -                 
klin                   -                 
molecule               {'co2': 0.0004}   
ng_adju                -                 
ng_refs                -                 
nv                     -                 
option_compute_btable  -                 
option_compute_ktable  -                 
option_wgt_flux        -                 
option_wgt_k           -                 
ref_pts                -                 
tsfc                   300               
vmax                   -                 
vmin                   -                 
w_diffuse              -                 
wgt                    -                 

                                                                \
                                                        LBLNEW   
atmpro                 trp                                       
band                   9                                         
commitnumber           a22ab94                                   
conc                   0.0004                                    
dv                     0.001                                     
klin                   6.5e-24                                   
molecule               co2                                       
ng_adju                [0, 0]                                    
ng_refs                [3, 3]                                    
nv                     1000                                      
option_compute_btable  0                                         
option_compute_ktable  0                                         
option_wgt_flux        1                                         
option_wgt_k           1                                         
ref_pts                [[1, 250], [50, 250]]                     
tsfc                   300                                       
vmax                   3000                                      
vmin                   1900                                      
w_diffuse              [[1.66, 1.66, 1.75], [1.75, 1.6, 1.85]]   
wgt                    [[0.7, 0.8, 0.7], [0.8, 0.7, 0.8]]        

                                                Fit parameters  
                                                      (co2, 9)  
atmpro                 mls                                      
band                   9                                        
commitnumber           a06b618                                  
conc                   0.0004                                   
dv                     0.001                                    
klin                   6.5e-24                                  
molecule               co2                                      
ng_adju                [0, 0]                                   
ng_refs                [3, 3]                                   
nv                     1000                                     
option_compute_btable  0                                        
option_compute_ktable  1                                        
option_wgt_flux        1                                        
option_wgt_k           1                                        
ref_pts                [(1, 250), (50, 250)]                    
tsfc                   294                                      
vmax                   3000                                     
vmin                   1900                                     
w_diffuse              [(1.66, 1.66, 1.75), (1.75, 1.6, 1.85)]  
wgt                    [(0.7, 0.8, 0.7), (0.8, 0.7, 0.8)]

CRD                 WGT igg=10                  CLIRAD  \
                  flug    fldg   fnetg       flug    fldg   fnetg    flug   
pressure level                                                              
0.00     1     -6.7094  0.0000 -6.7094 -6.6123     0.0000 -6.6123 -6.6096   
109.55   38    -6.6869  0.0048 -6.6821 -6.5797     0.0048 -6.5749 -6.5767   
1013.00  76    -8.1851  1.4862 -6.6990 -8.1851     1.6492 -6.5359 -8.1851   

                               CLIRAD - CRD                  
                  fldg   fnetg         flug    fldg   fnetg  
pressure level                                               
0.00     1      0.0000 -6.6096  0.0999       0.0000  0.0999  
109.55   38     0.0048 -6.5719  0.1102      -0.0000  0.1102  
1013.00  76     1.6513 -6.5338 -0.0000       0.1651  0.1651

--------------------------

### $CO_2$ overlapped with other gases

# 2 x $CO_2$

In [555]:
MOL = 'co2'
CONC = 2 * 400e-6
COMMITNUMBER = '1013f91'
NV, DV = 1000, .001
ATMPRO = dict(mls=294, saw=257, trp=300)

### Atmosphere compositions

We first set the concentration of CO2 to that double of the usual 4e-6 ppmv.  Then we split the overall composition into those where CO2 overlaps with other gases and those where only CO2 is present.

In [556]:
atmcomp = AtmComposition.cliradlw_nongreys()
atmcomp.gasconcs['co2'] = CONC
atmcomps_bft = [AtmComposition(gasconcs=atmcomp.gasconcs, gasinbands={b:[MOL]}) 
                for b, gs in atmcomp.gasinbands.items() if MOL in gs]
atmcomps_olp = [AtmComposition(gasconcs=atmcomp.gasconcs, gasinbands={b:gs})
                for b, gs in atmcomp.gasinbands.items() if MOL in gs and len(gs) > 1]

### $CO_2$-only 

In [557]:
for c in atmcomps_bft:
    for atmpro in ATMPRO.keys():
        pcli = c.to_cliradparam(commitnumber=COMMITNUMBER, atmpro=atmpro, tsfc=ATMPRO[atmpro])
        dcli = pcli.modeldata_pymongo(collection=CLIENT.cliradnew.lw)
    
        plbls = c.to_lblnewparam(bestfit_values=True, atmpro=atmpro, tsfc=ATMPRO[atmpro], nv=NV, dv=DV)
        plbl = plbls[0]
        #print(plbl.avail_commits(collection=CLIENT.lblnew.bestfit_lw))
        dlbl = plbl.modeldata_pymongo(collection=CLIENT.lblnew.bestfit_lw)
    
        ida = show_results(dlbl=dlbl, dcli=dcli, add_idanchor=True, atmpro=atmpro)
        remove_href(df=LINKS, idanchor=ida, dlbl=dlbl, dcli=dcli)
        show_href(df=LINKS, idanchor=ida, dlbl=dlbl, dcli=dcli)

-----------------------------

<a id="44755310735"></a>

[3] {'co2': 0.0008} mls

Run parameters  \
                                CLIRAD   
atmpro                 mls               
band                   [3]               
commitnumber           1013f91           
conc                   -                 
dv                     -                 
klin                   -                 
molecule               {'co2': 0.0008}   
ng_adju                -                 
ng_refs                -                 
nv                     -                 
option_compute_btable  -                 
option_compute_ktable  -                 
option_wgt_flux        -                 
option_wgt_k           -                 
ref_pts                -                 
tsfc                   294               
vmax                   -                 
vmin                   -                 
w_diffuse              -                 
wgt                    -                 

                                                                                 \
                                                                         LBLNEW   
atmpro                 mls                                                        
band                   3a                                                         
commitnumber           a22ab94                                                    
conc                   0.0008                                                     
dv                     0.001                                                      
klin                   6.37556e-24                                                
molecule               co2                                                        
ng_adju                [0, 0, 0]                                                  
ng_refs                [3, 2, 4]                                                  
nv                     1000                                                       
option_compute_btable  0                                                          
option_compute_ktable  0                                                          
option_wgt_flux        1                                                          
option_wgt_k           1                                                          
ref_pts                [[1, 250], [10, 250], [500, 250]]                          
tsfc                   294                                                        
vmax                   620                                                        
vmin                   540                                                        
w_diffuse              [[1.6, 1.6, 1.7], [1.75, 1.75], [1.55, 1.55, 1.6, 1.85]]   
wgt                    [[0.7, 0.3, 0.7], [0.7, 0.6], [0.4, 0.5, 0.8, 0.95]]       

                                                                 Fit parameters  
                                                                      (co2, 3a)  
atmpro                 mls                                                       
band                   3a                                                        
commitnumber           a06b618                                                   
conc                   0.0004                                                    
dv                     0.001                                                     
klin                   6.37556e-24                                               
molecule               co2                                                       
ng_adju                [0, 0, 0]                                                 
ng_refs                [3, 2, 4]                                                 
nv                     1000                                                      
option_compute_btable  0                                                         
option_compute_ktable  1                                                         
option_wgt_flux        1                                                         
option_wgt_k           1                  

CRD                   WGT igg=10                    \
                   flug     fldg    fnetg       flug     fldg    fnetg   
pressure level                                                           
0.000    1     -27.9753  0.0000  -27.9753 -28.0937    0.0000  -28.0937   
180.875  41    -28.3884  1.9204  -26.4680 -28.4860    1.9980  -26.4880   
1013.000 76    -36.2354  19.6810 -16.5544 -36.2354    19.8279 -16.4075   

                 CLIRAD                   CLIRAD - CRD                  
                   flug     fldg    fnetg         flug    fldg   fnetg  
pressure level                                                          
0.000    1     -28.0355  0.0000  -28.0355 -0.0602       0.0000 -0.0602  
180.875  41    -28.4362  2.0165  -26.4196 -0.0478       0.0961  0.0483  
1013.000 76    -36.2354  19.9515 -16.2839 -0.0000       0.2706  0.2706

...

<a id="08430172841"></a>

[11] {'co2': 0.0008} trp

Run parameters  \
                                CLIRAD   
atmpro                 trp               
band                   [11]              
commitnumber           1013f91           
conc                   -                 
dv                     -                 
klin                   -                 
molecule               {'co2': 0.0008}   
ng_adju                -                 
ng_refs                -                 
nv                     -                 
option_compute_btable  -                 
option_compute_ktable  -                 
option_wgt_flux        -                 
option_wgt_k           -                 
ref_pts                -                 
tsfc                   300               
vmax                   -                 
vmin                   -                 
w_diffuse              -                 
wgt                    -                 

                                                                \
                                                        LBLNEW   
atmpro                 trp                                       
band                   9                                         
commitnumber           a22ab94                                   
conc                   0.0008                                    
dv                     0.001                                     
klin                   6.5e-24                                   
molecule               co2                                       
ng_adju                [0, 0]                                    
ng_refs                [3, 3]                                    
nv                     1000                                      
option_compute_btable  0                                         
option_compute_ktable  0                                         
option_wgt_flux        1                                         
option_wgt_k           1                                         
ref_pts                [[1, 250], [50, 250]]                     
tsfc                   300                                       
vmax                   3000                                      
vmin                   1900                                      
w_diffuse              [[1.66, 1.66, 1.75], [1.75, 1.6, 1.85]]   
wgt                    [[0.7, 0.8, 0.7], [0.8, 0.7, 0.8]]        

                                                Fit parameters  
                                                      (co2, 9)  
atmpro                 mls                                      
band                   9                                        
commitnumber           a06b618                                  
conc                   0.0004                                   
dv                     0.001                                    
klin                   6.5e-24                                  
molecule               co2                                      
ng_adju                [0, 0]                                   
ng_refs                [3, 3]                                   
nv                     1000                                     
option_compute_btable  0                                        
option_compute_ktable  1                                        
option_wgt_flux        1                                        
option_wgt_k           1                                        
ref_pts                [(1, 250), (50, 250)]                    
tsfc                   294                                      
vmax                   3000                                     
vmin                   1900                                     
w_diffuse              [(1.66, 1.66, 1.75), (1.75, 1.6, 1.85)]  
wgt                    [(0.7, 0.8, 0.7), (0.8, 0.7, 0.8)]

CRD                 WGT igg=10                  CLIRAD  \
                  flug    fldg   fnetg       flug    fldg   fnetg    flug   
pressure level                                                              
0.00     1     -6.4971  0.0000 -6.4971 -6.4089     0.0000 -6.4089 -6.4055   
109.55   38    -6.4661  0.0055 -6.4606 -6.3645     0.0058 -6.3587 -6.3608   
1013.00  76    -8.1851  1.7164 -6.4687 -8.1851     1.8569 -6.3282 -8.1851   

                               CLIRAD - CRD                  
                  fldg   fnetg         flug    fldg   fnetg  
pressure level                                               
0.00     1      0.0000 -6.4055  0.0916       0.0000  0.0916  
109.55   38     0.0058 -6.3550  0.1052       0.0003  0.1056  
1013.00  76     1.8599 -6.3253 -0.0000       0.1435  0.1435

--------------------------

### $CO_2$ overlapped with other gases

In [558]:
for atmolp in atmcomps_olp:
    for atmpro in ATMPRO.keys():
        parm_cli = atmolp.to_cliradparam(commitnumber=COMMITNUMBER, atmpro=atmpro, tsfc=ATMPRO[atmpro])
        data_cli = parm_cli.modeldata_pymongo(collection=CLIENT.cliradnew.lw)
        
        parms_lbl = atmolp.to_lblnewparam(bestfit_values=True, atmpro=atmpro, tsfc=ATMPRO[atmpro], dv=DV, nv=NV)
        parm_lbl = parms_lbl[0]
        parm_lbl.avail_commits(collection=CLIENT.lblnew.overlap_lw)
        data_lbl = parm_lbl.modeldata_pymongo(collection=CLIENT.lblnew.overlap_lw)
        
        ida = show_results(dlbl=data_lbl, dcli=data_cli, add_idanchor=True, atmpro=atmpro)
        remove_href(df=LINKS, idanchor=ida, dlbl=data_lbl, dcli=data_cli)
        show_href(df=LINKS, idanchor=ida, dlbl=data_lbl, dcli=data_cli)

-----------------------------

<a id="61242327342"></a>

[3] {'h2o': 'atmpro', 'co2': 0.0008, 'n2o': 3.2e-07} mls

Run parameters  \
                                                                 CLIRAD   
atmpro                 mls                                                
band                   [3]                                                
commitnumber           1013f91                                            
conc                   -                                                  
dv                     -                                                  
klin                   -                                                  
molecule               {'h2o': 'atmpro', 'co2': 0.0008, 'n2o': 3.2e-07}   
ng_adju                -                                                  
ng_refs                -                                                  
nv                     -                                                  
option_compute_btable  -                                                  
option_compute_ktable  -                                                  
option_wgt_flux        -                                                  
option_wgt_k           -                                                  
ref_pts                -                                                  
tsfc                   294                                                
vmax                   -                                                  
vmin                   -                                                  
w_diffuse              -                                                  
wgt                    -                                                  

                                                                         \
                                                                 LBLNEW   
atmpro                 mls                                                
band                   3a                                                 
commitnumber           a22ab94                                            
conc                   -                                                  
dv                     0.001                                              
klin                   -                                                  
molecule               {'co2': 0.0008, 'h2o': 'atmpro', 'n2o': 3.2e-07}   
ng_adju                -                                                  
ng_refs                -                                                  
nv                     1000                                               
option_compute_btable  -                                                  
option_compute_ktable  -                                                  
option_wgt_flux        -                                                  
option_wgt_k           -                                                  
ref_pts                -                                                  
tsfc                   294                                                
vmax                   -                                                  
vmin                   -                                                  
w_diffuse              -                                                  
wgt                    -                                                  

                                                                 Fit parameters  \
                                                                      (co2, 3a)   
atmpro                 mls                                                        
band                   3a                                                         
commitnumber           a06b618                                                    
conc                   0.0004                                                     
dv                     0.001                                                      
klin                   6.37556e-24                                                
molecule               co2                                                        
ng_adju 

CRD                   WGT igg=10                    \
                   flug     fldg    fnetg       flug     fldg    fnetg   
pressure level                                                           
0.000    1     -23.8758  0.0000  -23.8758 -24.1750    0.0000  -24.1750   
180.875  41    -24.3447  2.1834  -22.1612 -24.6602    2.2563  -22.4040   
1013.000 76    -36.2354  34.9086 -1.3268  -36.2354    34.6115 -1.6239    

                 CLIRAD                   CLIRAD - CRD                  
                   flug     fldg    fnetg         flug    fldg   fnetg  
pressure level                                                          
0.000    1     -24.1264  0.0000  -24.1264 -0.2506       0.0000 -0.2506  
180.875  41    -24.6177  2.2746  -22.3430 -0.2730       0.0912 -0.1818  
1013.000 76    -36.2354  34.6469 -1.5885  -0.0000      -0.2617 -0.2617

...

<a id="35756755211"></a>

[11] {'h2o': 'atmpro', 'co2': 0.0008} trp

Run parameters  \
                                                 CLIRAD   
atmpro                 trp                                
band                   [11]                               
commitnumber           1013f91                            
conc                   -                                  
dv                     -                                  
klin                   -                                  
molecule               {'h2o': 'atmpro', 'co2': 0.0008}   
ng_adju                -                                  
ng_refs                -                                  
nv                     -                                  
option_compute_btable  -                                  
option_compute_ktable  -                                  
option_wgt_flux        -                                  
option_wgt_k           -                                  
ref_pts                -                                  
tsfc                   300                                
vmax                   -                                  
vmin                   -                                  
w_diffuse              -                                  
wgt                    -                                  

                                                         \
                                                 LBLNEW   
atmpro                 trp                                
band                   9                                  
commitnumber           a22ab94                            
conc                   -                                  
dv                     0.001                              
klin                   -                                  
molecule               {'co2': 0.0008, 'h2o': 'atmpro'}   
ng_adju                -                                  
ng_refs                -                                  
nv                     1000                               
option_compute_btable  -                                  
option_compute_ktable  -                                  
option_wgt_flux        -                                  
option_wgt_k           -                                  
ref_pts                -                                  
tsfc                   300                                
vmax                   -                                  
vmin                   -                                  
w_diffuse              -                                  
wgt                    -                                  

                                                Fit parameters  \
                                                      (co2, 9)   
atmpro                 mls                                       
band                   9                                         
commitnumber           a06b618                                   
conc                   0.0004                                    
dv                     0.001                                     
klin                   6.5e-24                                   
molecule               co2                                       
ng_adju                [0, 0]                                    
ng_refs                [3, 3]                                    
nv                     1000                                      
option_compute_btable  0                                         
option_compute_ktable  1                                         
option_wgt_flux        1                                         
option_wgt_k           1                                         
ref_pts                [(1, 250), (50, 250)]                     
tsfc                   294                                       
vmax                   3000                                      
vmin                   1900                                      
w_diffuse              [(1.66, 1.66, 1.75), (1.75, 1.6, 1.85)]   
wgt                    [(0.7, 0.8, 0.7), (0.8, 0.7, 0.8)]

CRD                 WGT igg=10                  CLIRAD  \
                  flug    fldg   fnetg       flug    fldg   fnetg    flug   
pressure level                                                              
0.00     1     -4.5762  0.0000 -4.5762 -4.4659     0.0000 -4.4659 -4.4591   
109.55   38    -4.5386  0.0058 -4.5328 -4.4188     0.0063 -4.4126 -4.4117   
1013.00  76    -8.1851  5.2917 -2.8934 -8.1851     5.3417 -2.8434 -8.1851   

                               CLIRAD - CRD                  
                  fldg   fnetg         flug    fldg   fnetg  
pressure level                                               
0.00     1      0.0000 -4.4591  0.1171       0.0000  0.1171  
109.55   38     0.0063 -4.4054  0.1269       0.0005  0.1274  
1013.00  76     5.3484 -2.8367 -0.0000       0.0567  0.0567

--------------------------

# 2 x $N_2O$ 

In [559]:
MOL = 'n2o'
CONC = 2 * 3.2e-7
COMMITNUMBER = ''
NV, DV = 1000, .001
ATMPRO = dict(mls=294, saw=257, trp=300)

### Atmospere composition

In [560]:
atmcomp = AtmComposition.cliradlw_nongreys()
atmcomp.gasconcs['n2o'] *= 2

atmcomps_bft = [AtmComposition(gasinbands={band:[MOL]}, gasconcs=atmcomp.gasconcs) 
                for band, gs in atmcomp.gasinbands.items() if MOL in gs]
atmcomps_olp = [AtmComposition(gasinbands={band:gs}, gasconcs=atmcomp.gasconcs)
                for band, gs in atmcomp.gasinbands.items() if MOL in gs and len(gs) > 1]

### $N_2O$-only

In [561]:
for c in atmcomps_bft:
    for atmpro in ATMPRO.keys():
        pcli = c.to_cliradparam(atmpro=atmpro, tsfc=ATMPRO[atmpro])
        #print(pcli.avail_commits(collection=CLIENT.cliradnew.lw))
        dcli = pcli.modeldata_pymongo(collection=CLIENT.cliradnew.lw, commits=['523cbb7'])
        
        plbls= c.to_lblnewparam(bestfit_values=True, nv=NV, dv=DV, atmpro=atmpro, tsfc=ATMPRO[atmpro])
        plbl = plbls[0]
        #print(plbl.avail_commits(collection=CLIENT.lblnew.bestfit_lw))
        dlbl = plbl.modeldata_pymongo(collection=CLIENT.lblnew.bestfit_lw, commits=['a22ab94'])
        
        ida = show_results(dlbl=dlbl, dcli=dcli, add_idanchor=True, atmpro=atmpro)
        remove_href(idanchor=ida, df=LINKS, dlbl=dlbl, dcli=dcli)
        show_href(idanchor=ida, df=LINKS, dlbl=dlbl, dcli=dcli)

-----------------------------

<a id="21425534233"></a>

[3] {'n2o': 6.4e-07} mls

Run parameters                          \
                                 CLIRAD                  LBLNEW   
atmpro                 mls               mls                      
band                   [3]               3a                       
commitnumber           523cbb7           a22ab94                  
conc                   -                 6.4e-07                  
dv                     -                 0.001                    
klin                   -                 2.22e-20                 
molecule               {'n2o': 6.4e-07}  n2o                      
ng_adju                -                 [0, 0]                   
ng_refs                -                 [1, 2]                   
nv                     -                 1000                     
option_compute_btable  -                 0                        
option_compute_ktable  -                 0                        
option_wgt_flux        -                 1                        
option_wgt_k           -                 1                        
ref_pts                -                 [[1, 250], [500, 250]]   
tsfc                   294               294                      
vmax                   -                 620                      
vmin                   -                 540                      
w_diffuse              -                 [[1.8], [1.66, 1.8]]     
wgt                    -                 [[0.9], [0.5, 0.95]]     

                               Fit parameters  
                                    (n2o, 3a)  
atmpro                 mls                     
band                   3a                      
commitnumber           a06b618                 
conc                   3.2e-07                 
dv                     0.001                   
klin                   2.22e-20                
molecule               n2o                     
ng_adju                [0, 0]                  
ng_refs                [1, 2]                  
nv                     1000                    
option_compute_btable  0                       
option_compute_ktable  1                       
option_wgt_flux        1                       
option_wgt_k           1                       
ref_pts                [(1, 250), (500, 250)]  
tsfc                   294                     
vmax                   620                     
vmin                   540                     
w_diffuse              [(1.8,), (1.66, 1.8)]   
wgt                    [(0.9,), (0.5, 0.95)]

CRD                  WGT igg=10                    CLIRAD  \
                   flug    fldg    fnetg       flug    fldg    fnetg     flug   
pressure level                                                                  
0.000    1     -34.2922  0.0000 -34.2922 -34.2789    0.0000 -34.2789 -34.2784   
180.875  41    -34.6831  0.4395 -34.2436 -34.6934    0.4261 -34.2673 -34.6934   
1013.000 76    -36.2354  4.2867 -31.9487 -36.2354    4.4511 -31.7843 -36.2354   

                                CLIRAD - CRD                  
                  fldg    fnetg         flug    fldg   fnetg  
pressure level                                                
0.000    1      0.0000 -34.2784  0.0137       0.0000  0.0137  
180.875  41     0.4262 -34.2672 -0.0103      -0.0133 -0.0236  
1013.000 76     4.4513 -31.7841 -0.0000       0.1646  0.1646

...

<a id="11784316658"></a>

[9] {'n2o': 6.4e-07} trp

Run parameters                             \
                                 CLIRAD                     LBLNEW   
atmpro                 trp               trp                         
band                   [9]               7                           
commitnumber           523cbb7           a22ab94                     
conc                   -                 6.4e-07                     
dv                     -                 0.001                       
klin                   -                 2.22e-20                    
molecule               {'n2o': 6.4e-07}  n2o                         
ng_adju                -                 [0, 0]                      
ng_refs                -                 [2, 2]                      
nv                     -                 1000                        
option_compute_btable  -                 0                           
option_compute_ktable  -                 0                           
option_wgt_flux        -                 1                           
option_wgt_k           -                 1                           
ref_pts                -                 [[1, 250], [500, 250]]      
tsfc                   300               300                         
vmax                   -                 1380                        
vmin                   -                 1215                        
w_diffuse              -                 [[1.8, 1.66], [1.6, 1.8]]   
wgt                    -                 [[0.6, 0.5], [0.6, 0.9]]    

                                  Fit parameters  
                                        (n2o, 7)  
atmpro                 mls                        
band                   7                          
commitnumber           a06b618                    
conc                   3.2e-07                    
dv                     0.001                      
klin                   2.22e-20                   
molecule               n2o                        
ng_adju                [0, 0]                     
ng_refs                [2, 2]                     
nv                     1000                       
option_compute_btable  0                          
option_compute_ktable  1                          
option_wgt_flux        1                          
option_wgt_k           1                          
ref_pts                [(1, 250), (500, 250)]     
tsfc                   294                        
vmax                   1380                       
vmin                   1215                       
w_diffuse              [(1.8, 1.66), (1.6, 1.8)]  
wgt                    [(0.6, 0.5), (0.6, 0.9)]

CRD                  WGT igg=10                    CLIRAD  \
                   flug    fldg    fnetg       flug    fldg    fnetg     flug   
pressure level                                                                  
0.00     1     -22.1211  0.0000 -22.1211 -21.4949    0.0000 -21.4949 -21.4913   
109.55   38    -22.2628  0.0686 -22.1942 -21.7077    0.0705 -21.6372 -21.7050   
1013.00  76    -26.9627  6.1111 -20.8517 -26.9627    6.4657 -20.4970 -26.9628   

                                CLIRAD - CRD                  
                  fldg    fnetg         flug    fldg   fnetg  
pressure level                                                
0.00     1      0.0000 -21.4913  0.6298       0.0000  0.6298  
109.55   38     0.0706 -21.6344  0.5578       0.0020  0.5597  
1013.00  76     6.4653 -20.4975 -0.0000       0.3542  0.3542

--------------------------

### $N_2O$ overlapped with other gases

In [562]:
for c in atmcomps_olp:
    for atmpro in ATMPRO.keys():
        pcli = c.to_cliradparam(atmpro=atmpro, tsfc=ATMPRO[atmpro], commitnumber='523cbb7')
        #print('cliradlw', pcli.avail_commits(collection=CLIENT.cliradnew.lw))
        dcli = pcli.modeldata_pymongo(collection=CLIENT.cliradnew.lw)
        
        plbls = c.to_lblnewparam(bestfit_values=True, nv=NV, dv=DV, atmpro=atmpro, tsfc=ATMPRO[atmpro], commitnumber='a22ab94')
        plbl = plbls[0]
        #print('lbl', plbl.avail_commits(collection=CLIENT.lblnew.overlap_lw))
        dlbl = plbl.modeldata_pymongo(collection=CLIENT.lblnew.overlap_lw)
        
        ida = show_results(dlbl=dlbl, dcli=dcli, add_idanchor=True, atmpro=atmpro)
        remove_href(idanchor=ida, df=LINKS, dlbl=dlbl, dcli=dcli)
        show_href(idanchor=ida, df=LINKS, dlbl=dlbl, dcli=dcli)

-----------------------------

<a id="53826615850"></a>

[3] {'co2': 0.0004, 'h2o': 'atmpro', 'n2o': 6.4e-07} mls

Run parameters  \
                                                                 CLIRAD   
atmpro                 mls                                                
band                   [3]                                                
commitnumber           523cbb7                                            
conc                   -                                                  
dv                     -                                                  
klin                   -                                                  
molecule               {'co2': 0.0004, 'h2o': 'atmpro', 'n2o': 6.4e-07}   
ng_adju                -                                                  
ng_refs                -                                                  
nv                     -                                                  
option_compute_btable  -                                                  
option_compute_ktable  -                                                  
option_wgt_flux        -                                                  
option_wgt_k           -                                                  
ref_pts                -                                                  
tsfc                   294                                                
vmax                   -                                                  
vmin                   -                                                  
w_diffuse              -                                                  
wgt                    -                                                  

                                                                         \
                                                                 LBLNEW   
atmpro                 mls                                                
band                   3a                                                 
commitnumber           a22ab94                                            
conc                   -                                                  
dv                     0.001                                              
klin                   -                                                  
molecule               {'co2': 0.0004, 'h2o': 'atmpro', 'n2o': 6.4e-07}   
ng_adju                -                                                  
ng_refs                -                                                  
nv                     1000                                               
option_compute_btable  -                                                  
option_compute_ktable  -                                                  
option_wgt_flux        -                                                  
option_wgt_k           -                                                  
ref_pts                -                                                  
tsfc                   294                                                
vmax                   -                                                  
vmin                   -                                                  
w_diffuse              -                                                  
wgt                    -                                                  

                                                                 Fit parameters  \
                                                                      (co2, 3a)   
atmpro                 mls                                                        
band                   3a                                                         
commitnumber           a06b618                                                    
conc                   0.0004                                                     
dv                     0.001                                                      
klin                   6.37556e-24                                                
molecule               co2                                                        
ng_adju 

CRD                   WGT igg=10                    \
                   flug     fldg    fnetg       flug     fldg    fnetg   
pressure level                                                           
0.000    1     -24.6167  0.0000  -24.6167 -24.8825    0.0000  -24.8825   
180.875  41    -25.1286  1.8098  -23.3188 -25.4174    1.8907  -23.5267   
1013.000 76    -36.2354  34.7166 -1.5189  -36.2354    34.4304 -1.8050    

                 CLIRAD                   CLIRAD - CRD                  
                   flug     fldg    fnetg         flug    fldg   fnetg  
pressure level                                                          
0.000    1     -24.8436  0.0000  -24.8436 -0.2270       0.0000 -0.2270  
180.875  41    -25.3827  1.9030  -23.4797 -0.2541       0.0932 -0.1609  
1013.000 76    -36.2354  34.4661 -1.7693  -0.0000      -0.2504 -0.2504

...

<a id="54132676335"></a>

[9] {'ch4': 1.8e-06, 'h2o': 'atmpro', 'n2o': 6.4e-07} trp

Run parameters  \
                                                                  CLIRAD   
atmpro                 trp                                                 
band                   [9]                                                 
commitnumber           523cbb7                                             
conc                   -                                                   
dv                     -                                                   
klin                   -                                                   
molecule               {'ch4': 1.8e-06, 'h2o': 'atmpro', 'n2o': 6.4e-07}   
ng_adju                -                                                   
ng_refs                -                                                   
nv                     -                                                   
option_compute_btable  -                                                   
option_compute_ktable  -                                                   
option_wgt_flux        -                                                   
option_wgt_k           -                                                   
ref_pts                -                                                   
tsfc                   300                                                 
vmax                   -                                                   
vmin                   -                                                   
w_diffuse              -                                                   
wgt                    -                                                   

                                                                          \
                                                                  LBLNEW   
atmpro                 trp                                                 
band                   7                                                   
commitnumber           a22ab94                                             
conc                   -                                                   
dv                     0.001                                               
klin                   -                                                   
molecule               {'ch4': 1.8e-06, 'h2o': 'atmpro', 'n2o': 6.4e-07}   
ng_adju                -                                                   
ng_refs                -                                                   
nv                     1000                                                
option_compute_btable  -                                                   
option_compute_ktable  -                                                   
option_wgt_flux        -                                                   
option_wgt_k           -                                                   
ref_pts                -                                                   
tsfc                   300                                                 
vmax                   -                                                   
vmin                   -                                                   
w_diffuse              -                                                   
wgt                    -                                                   

                                           Fit parameters  \
                                                 (ch4, 7)   
atmpro                 mls                                  
band                   7                                    
commitnumber           a06b618                              
conc                   1.8e-06                              
dv                     0.001                                
klin                   2e-21                                
molecule               ch4                                  
ng_adju                [0, 0]                               
ng_refs                [2, 3]                               
nv                     1000              

CRD                   WGT igg=10                    \
                   flug     fldg    fnetg       flug     fldg    fnetg   
pressure level                                                           
0.00     1     -12.5660  0.0000  -12.5660 -12.3329    0.0000  -12.3329   
109.55   38    -12.6877  0.1466  -12.5411 -12.5324    0.1611  -12.3713   
1013.00  76    -26.9627  23.3476 -3.6151  -26.9627    23.7068 -3.2559    

                 CLIRAD                   CLIRAD - CRD                  
                   flug     fldg    fnetg         flug    fldg   fnetg  
pressure level                                                          
0.00     1     -12.3127  0.0000  -12.3127  0.2534       0.0000  0.2534  
109.55   38    -12.5129  0.1613  -12.3516  0.1748       0.0148  0.1895  
1013.00  76    -26.9628  23.7312 -3.2315  -0.0000       0.3836  0.3836

--------------------------

# Fin

In [563]:
display.HTML('''<script>
code_show=true; 
function code_toggle() {
 if (code_show){
 $('div.input').hide();
 } else {
 $('div.input').show();
 }
 code_show = !code_show
} 
$( document ).ready(code_toggle);
</script>
<form action="javascript:code_toggle()"><input type="submit" value="Click here to toggle on/off the raw code."></form>''')
